In [6]:
import os
import sys
import json
from pathlib import Path

import yaml
from rich import print

In [2]:
class EmptyClass:
    pass

self = EmptyClass()
self.AD = EmptyClass()
self.AD.app_dir = '/mnt/ad_dev_conf/apps'

In [3]:
base_path = Path(self.AD.app_dir)

python_file_parents = set(
    f.parent.resolve()
    for f in base_path.rglob('*.py')
)
print('Python parents:')
print('\n'.join(f' - {p.as_posix()}' for p in python_file_parents))

module_parents = set(
    p for p in python_file_parents
    if not (p / '__init__.py').exists()
)
print('Module parents:')
print('\n'.join(f' - {p.as_posix()}' for p in module_parents))

package_parents = set(
    p for p in python_file_parents
    if (p / '__init__.py').exists()
)
print('Package parents:')
print('\n'.join(f' - {p.as_posix()}' for p in package_parents))

top_packages_dirs = set(
    p for p in package_parents
    if not (p.parent / '__init__.py').exists()
)
print('Top package parents:')
print('\n'.join(f' - {p.as_posix()}' for p in top_packages_dirs))

import_dirs = module_parents | set(p.parent for p in top_packages_dirs)
print('Imports')
print('\n'.join(f' - {p.as_posix()}' for p in import_dirs))

Python parents:

- /mnt/ad_dev_conf/apps/my_repo/my_pkg
 - /mnt/ad_dev_conf/apps
 - /mnt/ad_dev_conf/apps/my_repo/my_pkg/my_sub_pkg

Module parents:

- /mnt/ad_dev_conf/apps

Package parents:

- /mnt/ad_dev_conf/apps/my_repo/my_pkg
 - /mnt/ad_dev_conf/apps/my_repo/my_pkg/my_sub_pkg

Top package parents:

- /mnt/ad_dev_conf/apps/my_repo/my_pkg

Imports

- /mnt/ad_dev_conf/apps
 - /mnt/ad_dev_conf/apps/my_repo

In [4]:
association = {}
for dir in top_packages_dirs:
    associated_modules = list(dir.rglob('*.py'))
    # print('\n'.join(f' - {p.as_posix()}' for p in associated_modules))
    for module_file in associated_modules:
        association[module_file] = dir.stem

print(association)

{
    PosixPath('/mnt/ad_dev_conf/apps/my_repo/my_pkg/__init__.py'): 'my_pkg',
    PosixPath('/mnt/ad_dev_conf/apps/my_repo/my_pkg/motion.py'): 'my_pkg',
    PosixPath('/mnt/ad_dev_conf/apps/my_repo/my_pkg/my_sub_pkg/__init__.py'): 'my_pkg',
    PosixPath('/mnt/ad_dev_conf/apps/my_repo/my_pkg/my_sub_pkg/hello.py'): 'my_pkg'
}

In [15]:
module_name = 'my_pkg'

with Path('apps/apps.yaml').open('r') as f:
    self.app_config = yaml.load(f, Loader=yaml.SafeLoader)

self.non_apps = []

[
    app_name
    for app_name, app_cfg in self.app_config.items()
    if app_cfg['module'].split('.')[0] == module_name
]

['hello_sub', 'motion']